<a href="https://colab.research.google.com/github/LauraMartinus/ukuxhumana/blob/master/zulu_bpe_vs_morfessor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Pytorch

In [1]:
# http://pytorch.org/
from os.path import exists
from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())
cuda_output = !ldconfig -p|grep cudart.so|sed -e 's/.*\.\([0-9]*\)\.\([0-9]*\)$/cu\1\2/'
accelerator = cuda_output[0] if exists('/dev/nvidia0') else 'cpu'

!pip install -q http://download.pytorch.org/whl/{accelerator}/torch-0.4.1-{platform}-linux_x86_64.whl torchvision
import torch

tcmalloc: large alloc 1073750016 bytes == 0x57c76000 @  0x7fd0ad9962a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641


## Fairseq

In [2]:
!git clone https://github.com/pytorch/fairseq.git
import os
os.chdir("fairseq/")
!pip install -r requirements.txt
%run -i 'setup.py' build develop

Cloning into 'fairseq'...
remote: Enumerating objects: 45, done.
remote: Counting objects: 100% (45/45), done.
remote: Compressing objects: 100% (36/36), done.
remote: Total 3020 (delta 16), reused 16 (delta 9), pack-reused 2975
Receiving objects: 100% (3020/3020), 3.08 MiB | 19.72 MiB/s, done.
Resolving deltas: 100% (2191/2191), done.
    100% |████████████████████████████████| 430kB 6.5MB/s 
    100% |████████████████████████████████| 163kB 6.8MB/s 
  Running setup.py bdist_wheel for pycparser ... - \ | done
  Stored in directory: /root/.cache/pip/wheels/f2/9a/90/de94f8556265ddc9d9c8b271b0f63e57b26fb1d67a45564511
Successfully built pycparser
running build
running build_py
creating build
creating build/lib.linux-x86_64-3.6
creating build/lib.linux-x86_64-3.6/tests
copying tests/test_dictionary.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_backtranslation_dataset.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_sequence_scorer.py -> build/lib.linux-x86_64-3.6

## Subword

In [0]:
!git clone https://github.com/rsennrich/subword-nmt

Cloning into 'subword-nmt'...
remote: Enumerating objects: 481, done.
remote: Total 481 (delta 0), reused 0 (delta 0), pack-reused 481
Receiving objects: 100% (481/481), 203.75 KiB | 11.98 MiB/s, done.
Resolving deltas: 100% (287/287), done.


## BPE

In [0]:
os.chdir('../')
!cat enzu_parallel.train.en enzu_parallel.train.zu > combine.txt

!fairseq/subword-nmt/learn_bpe.py -s 8000 <combine.txt> enzu.codes
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.train.zu > train.zu
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.dev.zu > valid.zu
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.test.zu > test.zu

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang zu --target-lang en --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/enzu

!mkdir -p checkpoint/fconv
!python train.py data-bin/enzu \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 2000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/enzu --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang zu --target-lang en

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='enzu.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Pleas

## Morfessor

In [0]:
##NEED TO CHANGE FILE NAMES
TEXT=".."
%run 'preprocess.py' --source-lang zu --target-lang en --trainpref $TEXT/enzu_parallel.train.decomp --validpref $TEXT/enzu_parallel.dev.decomp --testpref $TEXT/enzu_parallel.test.decomp --destdir data-bin/de_enzu

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_enzu \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 500 \
    --arch fconv --save-dir chckpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_enzu --path chckpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang zu --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_enzu', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='zu', srcdict=None, target_lang='en', testpref='../enzu_parallel.test.decomp', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../enzu_parallel.train.decomp', validpref='../enzu_parallel.dev.decomp', workers=1)
| [zu] Dictionary: 14303 types
| [zu] ../enzu_parallel.train.decomp.zu: 18709 sents, 471069 tokens, 0.0% replaced by <unk>
| [zu] Dictionary: 14303 types
| [zu] ../enzu_parallel.dev.decomp.zu: 5019 sents, 133580 tokens, 1.46% replaced by <unk>
| [zu] Dictionary: 14303 types
| [zu] ../enzu_parallel.test.decomp.zu: 3000 sents, 86654 tokens, 1.91% replaced by <unk>
| [en] Dictionary: 27351 types
| [en] ../enzu_parallel.train.decomp.en: 18709 sents, 354198 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 27351 types
| [en] ../enzu_parallel.dev.decomp.en: 5019 sents, 109187 tokens, 3.66% replaced 

## BPE Eng Morfessor Zu

In [0]:
os.chdir('../')
#!cat enzu_parallel.train.en enzu_parallel.train.zu > combine.txt

!fairseq/subword-nmt/learn_bpe.py -s 12000 <enzu_parallel.train.en> enzu.codes
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.train.en > enzu_parallel.train.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.train.zu > train.zu
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.dev.en > enzu_parallel.dev.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.dev.zu > valid.zu
!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.test.en > enzu_parallel.test.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.test.zu > test.zu
os.chdir('fairseq/')

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='enzu.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Pleas

In [0]:
TEXT=".."
%run 'preprocess.py' --source-lang zu --target-lang en --trainpref $TEXT/enzu_parallel.train.decomp --validpref $TEXT/enzu_parallel.dev.decomp --testpref $TEXT/enzu_parallel.test.decomp --destdir data-bin/de_enzu

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_enzu \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 500 \
    --arch fconv --save-dir chkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_enzu --path chkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang zu --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_enzu', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='zu', srcdict=None, target_lang='en', testpref='../enzu_parallel.test.decomp', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../enzu_parallel.train.decomp', validpref='../enzu_parallel.dev.decomp', workers=1)
| [zu] Dictionary: 13247 types
| [zu] ../enzu_parallel.train.decomp.zu: 18709 sents, 476512 tokens, 0.0% replaced by <unk>
| [zu] Dictionary: 13247 types
| [zu] ../enzu_parallel.dev.decomp.zu: 5019 sents, 145320 tokens, 0.0186% replaced by <unk>
| [zu] Dictionary: 13247 types
| [zu] ../enzu_parallel.test.decomp.zu: 3000 sents, 95674 tokens, 0.0167% replaced by <unk>
| [en] Dictionary: 11607 types
| [en] ../enzu_parallel.train.decomp.en: 18709 sents, 406836 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 11607 types
| [en] ../enzu_parallel.dev.decomp.en: 5019 sents, 123889 tokens, 0.102% repl

# Clean


In [3]:
TEXT=".."
%run 'preprocess.py' --source-lang zu --target-lang en --trainpref $TEXT/enzu_parallel.train --validpref $TEXT/enzu_parallel.dev --testpref $TEXT/enzu_parallel.test --destdir data-bin/de_enzu

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_enzu \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 2000 \
    --arch fconv --save-dir chckpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_enzu --path chckpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang zu --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_enzu', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='zu', srcdict=None, target_lang='en', testpref='../enzu_parallel.test', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../enzu_parallel.train', validpref='../enzu_parallel.dev', workers=1)
| [zu] Dictionary: 68503 types
| [zu] ../enzu_parallel.train.zu: 18709 sents, 272277 tokens, 0.0% replaced by <unk>
| [zu] Dictionary: 68503 types
| [zu] ../enzu_parallel.dev.zu: 5019 sents, 78658 tokens, 21.6% replaced by <unk>
| [zu] Dictionary: 68503 types
| [zu] ../enzu_parallel.test.zu: 3000 sents, 50653 tokens, 21.8% replaced by <unk>
| [en] Dictionary: 27351 types
| [en] ../enzu_parallel.train.en: 18709 sents, 354198 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 27351 types
| [en] ../enzu_parallel.dev.en: 5019 sents, 109187 tokens, 3.66% replaced by <unk>
| [en] Dictionary: 27351 types
| [en] ../enzu_pa

## Results


BPE 4k: 5.13


Morfessor: 2.38

BPE english 8k, Morfessor Zulu: 5.06

Clean: 0.95